In [5]:
######### FILTER PACKAGE WARNINGS ########

import warnings  # Turn Off Frequent Warnings from Packages
warnings.filterwarnings("ignore", category=DeprecationWarning)


###### PYTHON VERSION COMPATIBILITY ######

from __future__ import print_function  # print() Function in Python 2

try:
    input = raw_input  # 'input' Function in Python 2 & 3
except NameError:
    pass


########## MACHINE LEARNING APIs ##########

# SCIKIT-LEARN
import sklearn
from sklearn.ensemble import RandomForestClassifier
from sklearn.feature_selection import chi2, f_classif, f_regression, RFECV, SelectKBest
from sklearn.metrics import accuracy_score, confusion_matrix, f1_score, log_loss, mean_squared_error
from sklearn.model_selection import KFold, train_test_split
from sklearn.neighbors import NearestNeighbors
from sklearn.neighbors import KNeighborsRegressor
from sklearn.preprocessing import Imputer, LabelEncoder



############ DATA & MANIPULATION ##########

import numpy as np
from random import setstate, shuffle

# Turn Off Deprecation & Future Warnings from Pandas
with warnings.catch_warnings():
    warnings.filterwarnings("ignore",category=DeprecationWarning)
    warnings.filterwarnings("ignore",category=FutureWarning)
    import pandas as pd

# Display All Rows & Columns in DataFrame
pd.set_option('display.max_rows', None) 
pd.set_option('display.max_columns', None)

# Pandas for Geographical Data
import geopandas
from shapely.geometry import Point

################ PLOTTING ################

# Opening & Manipulating Images
import PIL.Image
from scipy.ndimage.interpolation import rotate

# SEABORN
import seaborn as sns

# MATPLOTLIB
import matplotlib
import matplotlib.cm as cm
from matplotlib.colors import Normalize
from matplotlib.colorbar import ColorbarBase
from matplotlib.ticker import NullFormatter
from matplotlib.patches import Ellipse, Circle
import matplotlib.pyplot as plt
from matplotlib import animation, rc
from IPython.display import HTML, Image
%matplotlib inline

# equivalent to rcParams['animation.html'] = 'html5'
rc('animation', html='html5')

font = {'family' : 'serif',
        'weight' : 'normal',
        'size'   : 22}

matplotlib.rc('font', **font)
#import matplotlib.patches as patches


############# FILE MANAGEMENT #############

import errno
import io
import os
import urllib.request

#### Define file name & location.

In [6]:
directory    = 'data'
dict_file    = 'county_facts_dictionary.csv'
county_file  = 'county_facts.csv'
results_file = '2016_US_County_Level_Presidential_Results.csv'

#### Load data into a pandas dataframe.

In [7]:
dict_data    = pd.read_csv(os.path.join(directory, dict_file),    sep=',')
county_data  = pd.read_csv(os.path.join(directory, county_file),  sep=',')
results_data = pd.read_csv(os.path.join(directory, results_file), sep=',')

#### Available Features

In [8]:
dict_data

column_name                                        description
0    PST045214                          Population, 2014 estimate
1    PST040210          Population, 2010 (April 1) estimates base
2    PST120214  Population, percent change - April 1, 2010 to ...
3    POP010210                                   Population, 2010
4    AGE135214               Persons under 5 years, percent, 2014
5    AGE295214              Persons under 18 years, percent, 2014
6    AGE775214           Persons 65 years and over, percent, 2014
7    SEX255214                      Female persons, percent, 2014
8    RHI125214                         White alone, percent, 2014
9    RHI225214     Black or African American alone, percent, 2014
10   RHI325214  American Indian and Alaska Native alone, perce...
11   RHI425214                         Asian alone, percent, 2014
12   RHI525214  Native Hawaiian and Other Pacific Islander alo...
13   RHI625214                   Two or More Races, percent, 2014
14   RHI725214                  Hispanic or Latino, percent, 2014
15   RHI825214  White alone, not Hispanic or Latino, percent, ...
16   POP715213  Living in same house 1 year & over, percent, 2...
17   POP645213           Foreign born persons, percent, 2009-2013
18   POP815213  Language other than English spoken at home, pc...
19   EDU635213  High school graduate or higher, percent of per...
20   EDU685213  Bachelor's degree or higher, percent of person...
21   VET605213                                Veterans, 2009-2013
22   LFE305213  Mean travel time to work (minutes), workers ag...
23   HSG010214                                Housing units, 2014
24   HSG445213                      Homeownership rate, 2009-2013
25   HSG096213  Housing units in multi-unit structures, percen...
26   HSG495213  Median value of owner-occupied housing units, ...
27   HSD410213                              Households, 2009-2013
28   HSD310213                   Persons per household, 2009-2013
29   INC910213  Per capita money income in past 12 months (201...
30   INC110213                 Median household income, 2009-2013
31   PVY020213    Persons below poverty level, percent, 2009-2013
32   BZA010213               Private nonfarm establishments, 2013
33   BZA110213                  Private nonfarm employment,  2013
34   BZA115213  Private nonfarm employment, percent change, 20...
35   NES010213                   Nonemployer establishments, 2013
36   SBO001207                        Total number of firms, 2007
37   SBO315207                   Black-owned firms, percent, 2007
38   SBO115207  American Indian- and Alaska Native-owned firms...
39   SBO215207                   Asian-owned firms, percent, 2007
40   SBO515207  Native Hawaiian- and Other Pacific Islander-ow...
41   SBO415207                Hispanic-owned firms, percent, 2007
42   SBO015207                   Women-owned firms, percent, 2007
43   MAN450207             Manufacturers shipments, 2007 ($1,000)
44   WTN220207           Merchant wholesaler sales, 2007 ($1,000)
45   RTN130207                        Retail sales, 2007 ($1,000)
46   RTN131207                      Retail sales per capita, 2007
47   AFN120207  Accommodation and food services sales, 2007 ($...
48   BPS030214                             Building permits, 2014
49   LND110210                    Land area in square miles, 2010
50   POP060210                   Population per square mile, 2010

#### Preview the Population Demographics Data

In [9]:
county_data.head(10)

fips       area_name state_abbreviation  PST045214  PST040210  PST120214  \
0     0   United States                NaN  318857056  308758105        3.3   
1  1000         Alabama                NaN    4849377    4780127        1.4   
2  1001  Autauga County                 AL      55395      54571        1.5   
3  1003  Baldwin County                 AL     200111     182265        9.8   
4  1005  Barbour County                 AL      26887      27457       -2.1   
5  1007     Bibb County                 AL      22506      22919       -1.8   
6  1009   Blount County                 AL      57719      57322        0.7   
7  1011  Bullock County                 AL      10764      10915       -1.4   
8  1013   Butler County                 AL      20296      20946       -3.1   
9  1015  Calhoun County                 AL     115916     118586       -2.3   

   POP010210  AGE135214  AGE295214  AGE775214  SEX255214  RHI125214  \
0  308745538        6.2       23.1       14.5       50.8       77.4   
1    4779736        6.1       22.8       15.3       51.5       69.7   
2      54571        6.0       25.2       13.8       51.4       77.9   
3     182265        5.6       22.2       18.7       51.2       87.1   
4      27457        5.7       21.2       16.5       46.6       50.2   
5      22915        5.3       21.0       14.8       45.9       76.3   
6      57322        6.1       23.6       17.0       50.5       96.0   
7      10914        6.3       21.4       14.9       45.3       26.9   
8      20947        6.1       23.6       18.0       53.6       53.9   
9     118572        5.7       22.2       16.0       51.8       75.8   

   RHI225214  RHI325214  RHI425214  RHI525214  RHI625214  RHI725214  \
0       13.2        1.2        5.4        0.2        2.5       17.4   
1       26.7        0.7        1.3        0.1        1.5        4.1   
2       18.7        0.5        1.1        0.1        1.8        2.7   
3        9.6        0.7        0.9        0.1        1.6        4.6   
4       47.6        0.6        0.5        0.2        0.9        4.5   
5       22.1        0.4        0.2        0.1        0.9        2.1   
6        1.8        0.6        0.3        0.1        1.2        8.7   
7       70.1        0.8        0.3        0.7        1.1        7.5   
8       44.0        0.4        0.9        0.0        0.8        1.2   
9       21.1        0.5        0.9        0.1        1.7        3.5   

   RHI825214  POP715213  POP645213  POP815213  EDU635213  EDU685213  \
0       62.1       84.9       12.9       20.7       86.0       28.8   
1       66.2       85.0        3.5        5.2       83.1       22.6   
2       75.6       85.0        1.6        3.5       85.6       20.9   
3       83.0       82.1        3.6        5.5       89.1       27.7   
4       46.6       84.8        2.9        5.0       73.7       13.4   
5       74.5       86.6        1.2        2.1       77.5       12.1   
6       87.8       88.7        4.3        7.3       77.0       12.1   
7       22.1       84.7        5.4        5.2       67.8       12.5   
8       53.1       94.6        0.8        1.7       76.3       14.0   
9       72.9       83.6        2.4        4.5       78.6       16.1   

   VET605213  LFE305213  HSG010214  HSG445213  HSG096213  HSG495213  \
0   21263779       25.5  133957180       64.9       26.0     176700   
1     388865       24.2    2207912       69.7       15.9     122500   
2       5922       26.2      22751       76.8        8.3     136200   
3      19346       25.9     107374       72.6       24.4     168600   
4       2120       24.6      11799       67.7       10.6      89200   
5       1327       27.6       8978       79.0        7.3      90500   
6       4540       33.9      23826       81.0        4.5     117100   
7        636       26.9       4461       74.3        8.7      70600   
8       1497       24.0       9916       70.3       13.3      74700   
9      11385       22.5      53289       68.7       13.8     100600   

   HS

#### Preview the Election Results Data

In [10]:
results_data.head(10)

Unnamed: 0  votes_dem  votes_gop  total_votes   per_dem  per_gop    diff  \
0           0    93003.0   130413.0     246588.0  0.377159  0.52887  37,410   
1           1    93003.0   130413.0     246588.0  0.377159  0.52887  37,410   
2           2    93003.0   130413.0     246588.0  0.377159  0.52887  37,410   
3           3    93003.0   130413.0     246588.0  0.377159  0.52887  37,410   
4           4    93003.0   130413.0     246588.0  0.377159  0.52887  37,410   
5           5    93003.0   130413.0     246588.0  0.377159  0.52887  37,410   
6           6    93003.0   130413.0     246588.0  0.377159  0.52887  37,410   
7           7    93003.0   130413.0     246588.0  0.377159  0.52887  37,410   
8           8    93003.0   130413.0     246588.0  0.377159  0.52887  37,410   
9           9    93003.0   130413.0     246588.0  0.377159  0.52887  37,410   

  per_point_diff state_abbr county_name  combined_fips  
0         15.17%         AK      Alaska           2013  
1         15.17%         AK      Alaska           2016  
2         15.17%         AK      Alaska           2020  
3         15.17%         AK      Alaska           2050  
4         15.17%         AK      Alaska           2060  
5         15.17%         AK      Alaska           2068  
6         15.17%         AK      Alaska           2070  
7         15.17%         AK      Alaska           2090  
8         15.17%         AK      Alaska           2100  
9         15.17%         AK      Alaska           2105

In [25]:
results_data['candidate'] = 'Trump'
mask = results_data['per_dem'] > results_data['per_gop']
results_data.loc[mask, 'candidate']  = 'Clinton'

results_data['vote'] = 0
results_data.loc[mask, 'vote']  = 1

In [11]:
results_data.head()

Unnamed: 0  votes_dem  votes_gop  total_votes   per_dem  per_gop    diff  \
0           0    93003.0   130413.0     246588.0  0.377159  0.52887  37,410   
1           1    93003.0   130413.0     246588.0  0.377159  0.52887  37,410   
2           2    93003.0   130413.0     246588.0  0.377159  0.52887  37,410   
3           3    93003.0   130413.0     246588.0  0.377159  0.52887  37,410   
4           4    93003.0   130413.0     246588.0  0.377159  0.52887  37,410   

  per_point_diff state_abbr county_name  combined_fips  
0         15.17%         AK      Alaska           2013  
1         15.17%         AK      Alaska           2016  
2         15.17%         AK      Alaska           2020  
3         15.17%         AK      Alaska           2050  
4         15.17%         AK      Alaska           2060

#### Join Population Demographics & Election Results Dataframes on FIPS

In [12]:
results = results_data.drop(["Unnamed: 0", "state_abbr", "county_name"], axis=1)
results = county_data.set_index('fips').join(results.set_index('combined_fips'))

In [13]:
results.head(100)

area_name state_abbreviation  PST045214  \
fips                                                                    
0                         United States                NaN  318857056   
1000                            Alabama                NaN    4849377   
1001                     Autauga County                 AL      55395   
1003                     Baldwin County                 AL     200111   
1005                     Barbour County                 AL      26887   
1007                        Bibb County                 AL      22506   
1009                      Blount County                 AL      57719   
1011                     Bullock County                 AL      10764   
1013                      Butler County                 AL      20296   
1015                     Calhoun County                 AL     115916   
1017                    Chambers County                 AL      34076   
1019                    Cherokee County                 AL      26037   
1021                     Chilton County                 AL      43931   
1023                     Choctaw County                 AL      13323   
1025                      Clarke County                 AL      24945   
1027                        Clay County                 AL      13552   
1029                    Cleburne County                 AL      15080   
1031                      Coffee County                 AL      50909   
1033                     Colbert County                 AL      54543   
1035                     Conecuh County                 AL      12670   
1037                       Coosa County                 AL      10886   
1039                   Covington County                 AL      37914   
1041                    Crenshaw County                 AL      13977   
1043                     Cullman County                 AL      81289   
1045                        Dale County                 AL      49484   
1047                      Dallas County                 AL      41711   
1049                      DeKalb County                 AL      71065   
1051                      Elmore County                 AL      80977   
1053                    Escambia County                 AL      37733   
1055                      Etowah County                 AL     103531   
1057                     Fayette County                 AL      16874   
1059                    Franklin County                 AL      31601   
1061                      Geneva County                 AL      26712   
1063                      Greene County                 AL       8553   
1065                        Hale County                 AL      15184   
1067                       Henry County                 AL      17190   
1069                     Houston County                 AL     104193   
1071                     Jackson County                 AL      52665   
1073                   Jefferson County                 AL     660793   
1075                       Lamar County                 AL      14086   
1077                  Lauderdale County                 AL      93096   
1079                    Lawrence County                 AL      33477   
1081                         Lee County                 AL     154255   
1083                   Limestone County                 AL      90787   
1085                     Lowndes County                 AL      10580   
1087                       Macon County                 AL      19425   
1089                     Madison County                 AL     350299   
1091                     Marengo County                 AL      20110   
1093                      Marion County                 AL      30271   
1095                    Marshall County                 AL      94636   
1097                      Mobile County                 AL     415123   
1099                      Monroe County                 AL      21947   
1101                  Montgomery County                 AL     226189   
1103           

#### Separate County-Level & State-Level Results

In [14]:
county_results = results[results['state_abbreviation'].notnull()]

In [15]:
state_results = results[results['state_abbreviation'].isnull()]

#### Label Encode Categorical Variables

In [16]:
le = LabelEncoder()
le.fit(county_results['state_abbreviation'])
county_results.loc[:,'state_idx'] = le.transform(county_results['state_abbreviation'])

/Users/jennifer_kadowaki/anaconda/lib/python3.6/site-packages/pandas/core/indexing.py:337: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[key] = _infer_fill_value(value)
/Users/jennifer_kadowaki/anaconda/lib/python3.6/site-packages/pandas/core/indexing.py:517: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[item] = s


### Features

In [17]:
all_features = county_data.columns

In [18]:
# Selected Features
sf = all_features[3:].append(pd.Index(['state_idx']))

In [19]:
# Label
label = 'vote'

In [20]:
county_results[sf]

PST045214  PST040210  PST120214  POP010210  AGE135214  AGE295214  \
fips                                                                      
1001       55395      54571        1.5      54571        6.0       25.2   
1003      200111     182265        9.8     182265        5.6       22.2   
1005       26887      27457       -2.1      27457        5.7       21.2   
1007       22506      22919       -1.8      22915        5.3       21.0   
1009       57719      57322        0.7      57322        6.1       23.6   
1011       10764      10915       -1.4      10914        6.3       21.4   
1013       20296      20946       -3.1      20947        6.1       23.6   
1015      115916     118586       -2.3     118572        5.7       22.2   
1017       34076      34170       -0.3      34215        5.9       21.4   
1019       26037      25986        0.2      25989        4.8       20.4   
1021       43931      43631        0.7      43643        6.4       24.2   
1023       13323      13858       -3.9      13859        4.9       20.6   
1025       24945      25840       -3.5      25833        5.6       22.6   
1027       13552      13932       -2.7      13932        5.3       21.6   
1029       15080      14972        0.7      14972        5.7       23.3   
1031       50909      49948        1.9      49948        6.1       23.7   
1033       54543      54428        0.2      54428        5.7       21.7   
1035       12670      13228       -4.2      13228        5.5       21.4   
1037       10886      11758       -7.4      11539        4.8       18.3   
1039       37914      37765        0.4      37765        5.9       22.1   
1041       13977      13906        0.5      13906        6.1       22.7   
1043       81289      80410        1.1      80406        5.9       22.5   
1045       49484      50251       -1.5      50251        6.3       23.6   
1047       41711      43820       -4.8      43820        6.7       25.2   
1049       71065      71115       -0.1      71109        6.2       24.7   
1051       80977      79296        2.1      79303        5.9       23.0   
1053       37733      38319       -1.5      38319        6.1       22.0   
1055      103531     104427       -0.9     104430        5.7       22.1   
1057       16874      17241       -2.1      17241        5.4       21.7   
1059       31601      31709       -0.3      31704        6.6       24.3   
1061       26712      26790       -0.3      26790        5.8       22.2   
1063        8553       9045       -5.4       9045        5.9       23.3   
1065       15184      15760       -3.7      15760        6.2       23.3   
1067       17190      17302       -0.6      17302        5.5       21.2   
1069      104193     101547        2.6     101547        6.2       23.7   
1071       52665      53226       -1.1      53227        5.4       21.7   
1073      660793     658350        0.4     658466        6.6       23.1   
1075       14086      14564       -3.3      14564        5.0       21.7   
1077       93096      92709        0.4      92709        5.2       20.5   
1079       33477      34339       -2.5      34339        5.3       21.7   
1081      154255     140296        9.9     140247        5.8       21.6   
1083       90787      82782        9.7      82782        5.9       23.4   
1085       10580      11299       -6.4      11299        6.7       23.1   
1087       19425      21450       -9.4      21452        4.7       18.3   
1089      350299     334811        4.6     334811        5.8       22.4   
1091       20110      21029       -4.4      21027        6.0       23.0   
1093       30271      30777       -1.6      30776        5.4       21.2   
1095       94636      93019        1.7      93019        6.6       24.5   
1097      415123     413143        0.5     412992        6.7       24.0   
1099       21947      23070       -4.9      23068        5.5       23.4   
1101      226189     229363       -1.4     229363        6.8       24.0   
1103      119607     119486     

In [21]:
sf

Index(['PST045214', 'PST040210', 'PST120214', 'POP010210', 'AGE135214',
       'AGE295214', 'AGE775214', 'SEX255214', 'RHI125214', 'RHI225214',
       'RHI325214', 'RHI425214', 'RHI525214', 'RHI625214', 'RHI725214',
       'RHI825214', 'POP715213', 'POP645213', 'POP815213', 'EDU635213',
       'EDU685213', 'VET605213', 'LFE305213', 'HSG010214', 'HSG445213',
       'HSG096213', 'HSG495213', 'HSD410213', 'HSD310213', 'INC910213',
       'INC110213', 'PVY020213', 'BZA010213', 'BZA110213', 'BZA115213',
       'NES010213', 'SBO001207', 'SBO315207', 'SBO115207', 'SBO215207',
       'SBO515207', 'SBO415207', 'SBO015207', 'MAN450207', 'WTN220207',
       'RTN130207', 'RTN131207', 'AFN120207', 'BPS030214', 'LND110210',
       'POP060210', 'state_idx'],
      dtype='object')

In [23]:
county_results = county_results.reset_index(drop=True)

In [1]:
def plot_feature_scores(feature_labels, fscores, plot_name="feature_scores.pdf"):

    def compute_upper_bound(fmax):
        if fmax == 0:
            return 0
        return 10**(int(round(np.log10(fmax)))-1) + round(fmax, -int(np.floor(np.log10(fmax))))
    
    
    bar_size    = 0.25
    pad_dist    = 3.5
    num_line    = 5
    score_min   = 0
    score_max   = compute_upper_bound(max(fscores))
    score_range = np.arange(0, score_max, score_max/num_line)
    
    
    fig, ax = plt.subplots(figsize=(8, len(fscores) * bar_size))
    plt.margins(y=0)

    rects = ax.barh(range(len(val)), val[::-1], color='blue')

    for rect in rects:
        ax.text(rect.get_width() + pad_dist, rect.get_y() + rect.get_height()/2.,
                    '%.1f' % rect.get_width(),
                    ha='center', va='center', size=12)

    for x in score_range:
        plt.axvline(x=x, color='g', linestyle='--')

    plt.axhline(y=len(val)-int(np.sqrt(len(val)))-0.5, color='r', linestyle='-')

    ax.set_xlim(0,score_max)
    ax.xaxis.set_label_position('top')
    ax.set_xticklabels(score_range, fontsize=12)
    ax.tick_params(labeltop=True, labelbottom=True)

    ax.set_yticks(range(len(val)))
    ax.set_yticklabels(tick_labels[::-1], rotation='horizontal', fontsize=12)

    ax.set_xlabel("Feature Scores", fontsize=18)
    ax.set_ylabel("Features", fontsize=18)

    plt.tight_layout()
    plt.savefig(plot_name, dpi=300)
    plt.show()
    plt.close()

In [2]:
def train_rfc(x_train, y_train, n_estimators=1000, plot_importance=False, plot_name='feature_scores.pdf'):
    
    """
    train_nearest_neighbor: Training the Nearest Neighbor Algorithm with the Training Set
    
    :params: (1) x_train - Independent Variable of the Training Set
             (2) y_train - Dependent Variable of the Training Set
             (3) n_estimators - Number of Decision Trees in Random Forest
   
    :returns: model  - Model Trained on x_train and y_train.
    
    """
    
    # Defining the Nearest Neighbor Algorithm for k-Neighbors
    rfc   = RandomForestClassifier(n_jobs=-1, n_estimators=n_estimators)

    # Training the Nearest Neighbor Algorithm with the Training Set
    model = rfc.fit(x_train, y_train)
    
    if plot_importance:
        feature_importances = pd.DataFrame(rfc.feature_importances_,
                                   index = x_train.columns,
                                   columns=['importance']).sort_values('importance', ascending=False)
    
        plot_feature_scores(feature_importances['importance'].index.values,
                            feature_importances['importance'].values,
                            plot_name)
    

    return model

In [3]:
def test_rfc(model, x_test, y_test=None, plot=True, file='rfc_results.pdf'):
    
    """
    test_nearest_neighbor: Computes the Predicted Values and Loss Function Associated with the k-Nearest Neighbors Algorithm.
    
    :params: (1) model   - Trained Model
             (2) x_test  - Independent Variable of the Test/Validation Set
             (3) y_test  - Dependent (True) Variable of the Test/Validation Set
             (4) plot    - Flag for Plotting Results of the Prediction
    
    :returns: (1) y_pred - Prediction / Values when x_test is applied to the model.
              (2) loss   - Value of Loss Function of y_test (i.e., true value) and the predicted value (2).
    """
        
        
    # Predicting the Redshift Values of the Test or Validation Set
    y_pred = model.predict(x_test)
    
    if y_test is None:
        return y_pred
    
    loss = log_loss(y_test, y_pred)
    
    ac   = accuracy_score(y_test, y_pred)
    print('Accuracy: {}'.format(np.round(ac,3)))
    
    if plot:
    
        cm = confusion_matrix(y_test, model.predict(x_test))
        ax = sns.heatmap(cm, annot=True, fmt="d")
        ax.set(xlabel='Predicted UDGs', ylabel='True UDGs', title='Confusion Matrix')

        figure = ax.get_figure()    
        figure.savefig(file, dpi=400)
        plt.show()
        plt.close()

    return y_pred, loss, ac

In [4]:
def cross_validation_rfc(X, y, n_estimators=1000, plot=True, file='cv_rfc.pdf',  # Data
                        kfolds=10, shuffle=True, state=0, verbose=True):         # Cross-Validation Parameters

    """
    cross_validation: Determines the Optimal Number of Nearest Neighbors & Evaluates the Model Performance
    
    :params: (1) X - 
             (2) y -
             (3) n_estimators -
             (4) plot -
             (5) file -
             (6) kfolds -
             (7) shuffle -
             (8) state - 
             (9) verbose -
    
    :returns: (1) y_true
              (2) y_pred
    """
    
    
    # Defines the Type of Cross-Validation
    kf = KFold(n_splits=kfolds, shuffle=shuffle, random_state=state)
    
    # Stores Model Selection & Model Performance Results
    y_true = pd.DataFrame()
    y_pred = pd.DataFrame()

    # Splits the Dataset into the Training & Validation/Test Sets
    # Cross Validation: Iterates through Each Fold
    for fold_idx, (train_idx, test_idx) in enumerate(kf.split(X=X, y=y)):

        # Prints Assignment for Training and Validation/Testing Set
        if verbose:
            print("\nFold {0}\n\tTEST: {1}\n".format(fold_idx, test_idx))
            
        # Computes
        model = train_rfc(pd.DataFrame(X, index=train_idx), pd.DataFrame(y, index=train_idx).values.ravel(),
                          n_estimators=n_estimators,
                          plot_importance=False,
                          plot_name='feature_scores'+str(fold_idx)+'.pdf')
        
        pred, loss, ac = test_rfc(model, x_test=pd.DataFrame(X, index=test_idx), y_test=pd.DataFrame(y, index=test_idx),
                                  plot=plot, file='rfc_results_{0}.pdf'.format(fold_idx))
        
        y_true = y_true.append(pd.DataFrame(y, index=test_idx))
        y_pred = y_pred.append(pd.DataFrame(pred))
        
        #show_tree(model, fold_idx)
        
    
    cm = confusion_matrix(y_true, y_pred)
    ax = sns.heatmap(cm, annot=True, fmt="d")
    ax.set(xlabel='Predicted UDGs', ylabel='True UDGs', title='Confusion Matrix')
    figure = ax.get_figure()    
    figure.savefig(file, dpi=400)
    plt.show()
    plt.close()

    print('Overall Accuracy: {}'.format(accuracy_score(y_true, y_pred)))
    
    return y_true, y_pred    

In [26]:
y_true, y_pred = cross_validation_rfc(county_results[sf].dropna(), county_results[label], plot=False, verbose=False)

KeyError: 'vote'

In [ ]:
county_results[sf].dtypes

In [ ]:
county_results[label].dtypes

In [ ]:
np.any(np.isnan(county_results[sf]))

In [ ]:
np.all(np.isfinite(county_results[sf]))

In [ ]:
np.where(np.isnan(county_results[sf]))